In [1]:
!pip install graphviz==0.10  
!apt-get install graphviz

Reading package lists... Done
Building dependency tree       
Reading state information... Done
graphviz is already the newest version (2.40.1-2).
The following package was automatically installed and is no longer required:
  libnvidia-common-440
Use 'apt autoremove' to remove it.
0 upgraded, 0 newly installed, 0 to remove and 39 not upgraded.


In [2]:
import pandas as pd
import numpy as np
# importando os dados 
dados = pd.read_csv("https://gist.githubusercontent.com/guilhermesilveira/4d1d4a16ccbf6ea4e0a64a38a24ec884/raw/afd05cb0c796d18f3f5a6537053ded308ba94bf7/car-prices.csv")
print(dados.head()) # print das primeiras inhas dos dados



   Unnamed: 0  mileage_per_year  model_year      price sold
0           0             21801        2000   30941.02  yes
1           1              7843        1998   40557.96  yes
2           2              7109        2006   89627.50   no
3           3             26823        2015   95276.14   no
4           4              7935        2014  117384.68  yes


In [3]:
# renomeando algumas colunas
a_renomear = {
    "mileage_per_year" : "milhas_por_ano",
    "model_year" : "ano_do_modelo",
    "price" : "preco",
    "sold" : "vendido"
}
dados = dados.rename(columns = a_renomear)


#como estamos trabalhando com classificaçãão binaria, vamos mudar o yes e no da ultima coluna para 0 ou 1

a_trocar = {
    "no" :0,
    "yes" :1
}

dados.vendido = dados.vendido.map(a_trocar)
dados.head()

Unnamed: 0  milhas_por_ano  ano_do_modelo      preco  vendido
0           0           21801           2000   30941.02        1
1           1            7843           1998   40557.96        1
2           2            7109           2006   89627.50        0
3           3           26823           2015   95276.14        0
4           4            7935           2014  117384.68        1

In [4]:
#no ano do modelo tem uma diferenca muito pequena entre os anos então vamos usar a coluna idade do carro

from datetime import datetime

dados['idade_do_modelo'] = datetime.today().year - dados.ano_do_modelo 
dados.head()

Unnamed: 0  milhas_por_ano  ...  vendido  idade_do_modelo
0           0           21801  ...        1               20
1           1            7843  ...        1               22
2           2            7109  ...        0               14
3           3           26823  ...        0                5
4           4            7935  ...        1                6

[5 rows x 6 columns]

In [5]:
# vamos mudar a unidade para km/ano ao invéés de milha/ano
dados['km_por_ano'] = dados.milhas_por_ano*(1.60934)
dados.head()

Unnamed: 0  milhas_por_ano  ...  idade_do_modelo   km_por_ano
0           0           21801  ...               20  35085.22134
1           1            7843  ...               22  12622.05362
2           2            7109  ...               14  11440.79806
3           3           26823  ...                5  43167.32682
4           4            7935  ...                6  12770.11290

[5 rows x 7 columns]

In [6]:
#drop das colunas que n sao necessarias
dados = dados.drop(columns = ["Unnamed: 0", "milhas_por_ano", "ano_do_modelo"], axis=1)
dados.head()


preco  vendido  idade_do_modelo   km_por_ano
0   30941.02        1               20  35085.22134
1   40557.96        1               22  12622.05362
2   89627.50        0               14  11440.79806
3   95276.14        0                5  43167.32682
4  117384.68        1                6  12770.11290

In [7]:
#classificando linearmente
x = dados[["preco","idade_do_modelo","km_por_ano"]]
y = dados["vendido"]

from sklearn.model_selection import train_test_split
from sklearn.svm import LinearSVC
from sklearn.metrics import accuracy_score
from sklearn.preprocessing import StandardScaler

SEED = 5
np.random.seed(SEED)
treinox, testex, treinoy, testey = train_test_split(x,y,test_size = 0.25, stratify = y)

#escalando os dados... criando um intervalo onde eles se encontram
#ou seja, tira a media e divide pelo desvio padrão
scaler = StandardScaler()
scaler.fit(treinox)
treinox_escalado = scaler.transform(treinox)
testex_escalado = scaler.transform(testex )


#gerando o modelo
modelo = LinearSVC()
modelo.fit(treinox_escalado,treinoy)
previsoes = modelo.predict(testex_escalado)

acuracia = accuracy_score(testey,previsoes)
print("acuracia usando LinearSVC: " )
print( acuracia)


acuracia usando LinearSVC: 
0.71


In [8]:
# acuracia de base para comparar
# vamos usar os estimadores bobos (dummy) para isso

from sklearn.dummy import DummyClassifier

dummy = DummyClassifier()
dummy.fit(treinox,treinoy)
previsoes = dummy.predict(testex)
acuracia = accuracy_score(testey,previsoes)
print("acuracia de base: ")
print(acuracia)

acuracia de base: 
0.5244


/usr/local/lib/python3.6/dist-packages/sklearn/dummy.py:132: FutureWarning: The default value of strategy will change from stratified to prior in 0.24.
  "stratified to prior in 0.24.", FutureWarning)


In [9]:
#agora vamos usar áárvores de decisoõões para classificar
#esses algoritmos de decisao retornam como foi decidido as escolhas

from sklearn.tree import DecisionTreeClassifier
#ATENÇÃÃO: as áárvores de decisãão nãão nessecitm de escaladores para funcionarem bem
modelo = DecisionTreeClassifier()
modelo.fit(treinox,treinoy)
previsoes = modelo.predict(testex)

acuracia = accuracy_score(testey,previsoes)
print("acuracia com arvore de decisao: " )
print( acuracia)

acuracia com arvore de decisao: 
0.7268


In [10]:
# para vizualizar graficamente a arvore de decisoes

from sklearn.tree import export_graphviz
import graphviz
features = x.columns
dot_data = export_graphviz(modelo, feature_names=features,filled=True, rounded=True, class_names=["nãão", "sim"]) # devolve o grafico em uma formataçao estranha


grafico = graphviz.Source(dot_data)
grafico


